<a href="https://colab.research.google.com/github/badabad/DS-Unit-2-Linear-Models/blob/master/Copy_of_LS_DS_212_assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 1, Module 2*

---

# Regression 2

## Assignment

You'll continue to **predict how much it costs to rent an apartment in NYC,** using the dataset from renthop.com.

- [ ] Do train/test split. Use data from April & May 2016 to train. Use data from June 2016 to test.
- [ ] Engineer at least two new features. (See below for explanation & ideas.)
- [ ] Fit a linear regression model with at least two features.
- [ ] Get the model's coefficients and intercept.
- [ ] Get regression metrics RMSE, MAE, and $R^2$, for both the train and test data.
- [ ] What's the best test MAE you can get? Share your score and features used with your cohort on Slack!
- [ ] As always, commit your notebook to your fork of the GitHub repo.


#### [Feature Engineering](https://en.wikipedia.org/wiki/Feature_engineering)

> "Some machine learning projects succeed and some fail. What makes the difference? Easily the most important factor is the features used." — Pedro Domingos, ["A Few Useful Things to Know about Machine Learning"](https://homes.cs.washington.edu/~pedrod/papers/cacm12.pdf)

> "Coming up with features is difficult, time-consuming, requires expert knowledge. 'Applied machine learning' is basically feature engineering." — Andrew Ng, [Machine Learning and AI via Brain simulations](https://forum.stanford.edu/events/2011/2011slides/plenary/2011plenaryNg.pdf) 

> Feature engineering is the process of using domain knowledge of the data to create features that make machine learning algorithms work. 

#### Feature Ideas
- Does the apartment have a description?
- How long is the description?
- How many total perks does each apartment have?
- Are cats _or_ dogs allowed?
- Are cats _and_ dogs allowed?
- Total number of rooms (beds + baths)
- Ratio of beds to baths
- What's the neighborhood, based on address or latitude & longitude?

## Stretch Goals
- [ ] If you want more math, skim [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf),  Chapter 3.1, Simple Linear Regression, & Chapter 3.2, Multiple Linear Regression
- [ ] If you want more introduction, watch [Brandon Foltz, Statistics 101: Simple Linear Regression](https://www.youtube.com/watch?v=ZkjP5RJLQF4)
(20 minutes, over 1 million views)
- [ ] Add your own stretch goal(s) !

In [3]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas-profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [33]:
import numpy as np
import pandas as pd

# Read New York City apartment rental listing data
df = pd.read_csv(DATA_PATH+'apartments/renthop-nyc.csv')
assert df.shape == (49352, 34)

# Remove the most extreme 1% prices,
# the most extreme .1% latitudes, &
# the most extreme .1% longitudes
df = df[(df['price'] >= np.percentile(df['price'], 0.5)) & 
        (df['price'] <= np.percentile(df['price'], 99.5)) & 
        (df['latitude'] >= np.percentile(df['latitude'], 0.05)) & 
        (df['latitude'] < np.percentile(df['latitude'], 99.95)) &
        (df['longitude'] >= np.percentile(df['longitude'], 0.05)) & 
        (df['longitude'] <= np.percentile(df['longitude'], 99.95))]

In [42]:
import pandas_profiling
df.profile_report()

In [77]:
df['pets allowed'] = df['dogs_allowed'] * df['cats_allowed']
df['entrance'] = df['doorman']*df['elevator']

In [44]:
df['created'] = pd.to_datetime(df['created'])

In [56]:
print(df.shape)
df = df.sort_values(by='created')
df.set_index('created', inplace=True)
df.head()

(48817, 36)


bathrooms  bedrooms  ... pets allowed bathroom ratio
created                                   ...                            
2016-04-01 22:12:41        1.0         1  ...            0            0.5
2016-04-01 22:56:00        1.0         0  ...            1            1.0
2016-04-01 22:57:15        2.0         3  ...            1            0.4
2016-04-01 23:26:07        1.0         1  ...            1            0.5
2016-04-02 00:48:13        1.0         1  ...            1            0.5

[5 rows x 35 columns]

In [57]:
df.tail()

bathrooms  bedrooms  ... pets allowed bathroom ratio
created                                   ...                            
2016-06-29 17:47:34        1.0         2  ...            0       0.333333
2016-06-29 17:56:12        1.0         1  ...            1       0.500000
2016-06-29 18:14:48        1.0         1  ...            1       0.500000
2016-06-29 18:30:41        1.0         3  ...            1       0.250000
2016-06-29 21:41:47        1.0         3  ...            0       0.250000

[5 rows x 35 columns]

In [79]:
#Split data
target = 'price'
features = ['pets allowed', 'entrance']

#cutoff- training set will be before month of july
y_train = df[target].loc['2016-04-01':'2016-05-30']
X_train = df[features].loc['2016-04-01':'2016-05-30']

#validation set will be month of july
y_val = df[target].loc['2016-06':]
X_val = df[features].loc['2016-06':]

In [80]:
X_train

pets allowed  entrance
created                                    
2016-04-01 22:12:41             0         1
2016-04-01 22:56:00             1         0
2016-04-01 22:57:15             1         1
2016-04-01 23:26:07             1         1
2016-04-02 00:48:13             1         1
...                           ...       ...
2016-05-30 16:24:15             0         0
2016-05-30 18:57:50             1         0
2016-05-30 20:05:21             1         1
2016-05-30 20:24:17             1         0
2016-05-30 20:46:36             1         1

[31839 rows x 2 columns]

In [81]:
X_val

pets allowed  entrance
created                                    
2016-06-01 01:10:37             0         0
2016-06-01 01:11:06             1         0
2016-06-01 01:11:12             1         0
2016-06-01 01:11:52             0         0
2016-06-01 01:12:22             1         0
...                           ...       ...
2016-06-29 17:47:34             0         0
2016-06-29 17:56:12             1         0
2016-06-29 18:14:48             1         0
2016-06-29 18:30:41             1         0
2016-06-29 21:41:47             0         0

[16973 rows x 2 columns]

In [85]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error

y_pred = [y_train.mean()]*len(y_train)
print('Baseline MAE:', mean_absolute_error(y_train,y_pred))

Baseline MAE: 1201.973180899577


In [83]:
from sklearn.linear_model import LinearRegression
model = LinearRegression()
model.fit(X_train,y_train)
y_pred = model.predict(X_train)

In [87]:
#check metrics
print('Training MAE:', mean_absolute_error(y_train, model.predict(X_train)))
print('Validation MAE:', mean_absolute_error(y_val, model.predict(X_val)))

print('Training RMSE:', mean_squared_error(y_train, model.predict(X_train)))
print('Validation RMSE:', mean_squared_error(y_val, model.predict(X_val)))

print('Training R2:', r2_score(y_train, model.predict(X_train)))
print('Validation R2:', r2_score(y_val, model.predict(X_val)))

Training MAE: 1163.5341303053046
Validation MAE: 1151.4133224712464
Training RMSE: 2905491.689569666
Validation RMSE: 2903399.3199058645
Training R2: 0.06436483421928219
Validation R2: 0.06583672707235944
